In [2]:
from scipy.stats import norm
from time import time
import random    
import pandas as pd
# Import des bibliothèques nécessaires

In [3]:
if False:
    !rm ./../logs/*

# -1) Cycliste

In [4]:
class logger(): ## A quoi sert la classe
    """
    Save data into memory (in an array) and write it down to a file after [nb_log] is reached.
    """
    def __init__(self, path, limit_to_save_to_disk=25, header=None): # Définition du constructeur
        import os.path
        self.path    = path # On crée une variable self.path et on lui donne comme valeur path
        self.limit   = limit_to_save_to_disk 
        self.logs    = [] ## Pour rentrer le log ? Qu'est ce que le log
        self.nb_logs = 0
        if header:
            if not os.path.isfile(path):
                with open(path, "a") as f:
                    f.write(header)
                    f.write("\n")
        
    def log(self, string):
        self.logs.append(string)
        self.nb_logs = self.nb_logs +1
        if self.limit < self.nb_logs:
            self.write_to_disk()
    
    def write_to_disk(self):
        from time import time
        heure = time()
        new_path = "%s_%s.csv"%(self.path, heure)
        #new_path = self.path # écrase la commande précédente. Laquelle choisir ?
        with open(new_path, "a") as f:
            while len(self.logs):
                try:
                    a = self.logs.pop()
                    f.write(u"%s\n"%a)
                except:
                    print ("pbm d'encodage avec la phrase :  "), # problème de parenthèse
                    print (a)
        self.nb_logs = len(self.logs)
    def __del__(self):
        self.write_to_disk()
        

In [5]:
import random

In [6]:
class Cycliste:

    def __init__(self, parameters):
        import time
        import random
        from scipy.stats import norm
        import random
        """ ==========================================================
                                    Variables
        ==============================================================="""
        ## A quoi servent ces variables ?
        homme   = "homme"
        femme   = "femme"
        age_min = 15 ## Pour quoi 15 ans minimum ? J'avais vu à partir de 14 ans
        age_max = 80
        sexe    = random.choice([homme, femme]) # choisit un élément aléatoire dans une liste
        age     = random.randint(age_min ,age_max)
        sportif = random.choice([-0.5, 0, 2, 4, 6 ]) # comment ont été choisis ces chiffres ?
        
        if   age < 35 : facteur = norm( loc =1.2, scale=0.2 ) ## Pourquoi ces valeurs ? Moyenne écart type ?
        elif age < 50 : facteur = norm( loc =1  , scale=0.2 )
        elif age < 90 : facteur = norm( loc =0.7, scale=0.2 )

        if sexe == homme:
            vitesse_de_base  = 20
            nb_km            = norm( loc =7, scale=4 )
        else:
            vitesse_de_base  = 15
            nb_km            = norm( loc =10, scale=4 )
        vitesse_moyenne      = vitesse_de_base * facteur.rvs(1) + sportif # rvs nous permet de choisir au hasard dans la variable facteur
        """ ==========================================================
                                    Attributs
        ==============================================================="""
        self.identifiant     = "cycliste_%s"%parameters[0] # Il va chercher où les paramètres ? Le premier indice
        self.station_maison  = parameters[1]
        self.station_travail = parameters[2]
        self.sportif         = sportif
        self.age             = age
        self.sexe            = sexe
        self.nb_km           = nb_km.rvs(1)[0]
        self.vitesse         = vitesse_moyenne[0]
        self.sur_velo        = False
        self.debug           = False
        self.nb_trajet       = 0
        self.durees          = []
        self.trajets         = []
        self.velo            = False
        self.prises          = []
        self.attente         = 0.5 ; #random.randint(0,10)
        self.last_rendu      = time.time()
        self.logger_cycliste = logger("./../logs/cycliste_cyclistes.csv", 0, header = "cycliste,sportif,age,sexe,nb_km,vitesse,attente"        )
        self.logger_prise    = logger("./../logs/cycliste_prises.csv", header = "cycliste,heure_de_depart,velo,action")
        self.logger_rendu    = logger("./../logs/cycliste_rendu.csv", header = "cycliste,heure_de_depart,heure_d_arrivee,nb_km_trajet,velo.nom")
        self.logger_debug    = logger("./../logs/cycliste_debug.csv",1, header = "cycliste,n_message,time,message")
        
        
        
        
        self.a_la_maison     = True
        self.n_message       = 0
        self.trajet_courant  = ""
        """ ==========================================================
                                    Logs
        ==============================================================="""        
        self.log_cycliste()
        self.logger_debug.log("cree")        
        self.log_debug(u"station_maison = %s"%self.station_maison)
        self.log_debug(u"station_travail = %s"%self.station_travail)
        self.log_debug(u"station_maison nearest= %s"%"|".join([x.nom for x in self.station_maison.nearest]))
        self.log_debug(u"station_travail nearest= %s"%"|".join([x.nom for x in self.station_travail.nearest]))
        
    def peut_prendre_velo(self, station):
        """
        Renvoie un velo ou bien False.
        """
        from time import time
        import random
        """ __________________________________________________________
                            Préconditions
        ______________________________________________________________"""        
        if time() < self.attente + self.last_rendu: ## A expliquer last_rendu : dernier rendu de vélo. Délai d'utilisation entre 2 prises de vélos ?
            self.log_debug(u"trop t ") # attente : temps de travail + heure du dernier rendu du vélo au travail
        if self.sur_velo:
            self.log_debug(u"en route")
            return False, False # Est ce que je peux avoir les 2 ? Trop tot et en route ?
        """ __________________________________________________________
                    Recherche de vélo sur les stations proches
        ______________________________________________________________"""        
        random.shuffle(station.nearest) # le nearest est calculé en fonction du lieu de travail et d'habitation ?
        for local_station in station.nearest:
            velo = local_station.prendre_velo()            
            if not velo: 
                self.log_debug(u"pas de velo sur la station %s " % local_station)
                continue
            if local_station in self.station_maison.nearest : elem_de = "station maison"
            else                                            : elem_de = "station travail"
            self.log_debug(u"velo pris sur station %s (elem de %s)" % (local_station,elem_de))
            return velo , local_station
        """ __________________________________________________________
                                    Aucun vélo trouvé
        ______________________________________________________________"""        
        self.log_debug(u"Aucun velo trouve aux alentours.")
        return False, False
    
    
    def prend_velo(self):
        import time
        
        if   self.a_la_maison : station = self.station_maison
        else                  : station = self.station_travail
        
        velo, station = self.peut_prendre_velo(station)
        if not velo :
            return 
                       
        self.log_debug(u"%s a pris le velo %s sur la station %s"%(self.a_la_maison, velo, station))
        velo.disponible      = False
        self.sur_velo        = True
        self.heure_de_depart = time.time()
        self.velo            = velo
        self.trajet_courant  = trajet(self, velo,station)
        self.log_prise()
        try:
            nb_km_local          = norm( loc =self.nb_km, scale=self.nb_km/float(3) ).rvs(1)[0] # Pourquoi ces paramètres ?
        except Exception as e:
            self.log_debug(u"pbm sur nb_km_local = self.nb_km = %s " %self.nb_km)
            nb_km_local = 15
        try:
            vitesse_local        = norm(loc = self.vitesse, scale = self.vitesse/float(10)).rvs(1)[0]
            vitesse_local        = vitesse_local * velo.performance
        except:
            self.log_debug(u"pbm sur vitesse_local self.vitesse = %s"%self.vitesse)
            vitesse_local = self.vitesse
            
        self.nb_km_trajet    = nb_km_local
        duree                = nb_km_local / vitesse_local
        self.heure_d_arrivee = self.heure_de_depart + duree
        
        if velo.performance <0.1:
            duree                = 0
            #self.durees.append( duree)
            self.heure_d_arrivee =  self.heure_de_depart # il n'est pas parti. Est ce qu'on part du principe que le vélo
            self.nb_km_trajet    = 0 # a été attribué et qu'il n'a pas bougé ou tout simplement qu'on ne l'a pas attribué
            self.log_debug(u"velo defaillant <0.1, rendu a la meme station :-( ")
            self.rendre_vite_velo(station)
            return
        
        self.a_la_maison = not self.a_la_maison
        if velo.performance <0.3: # Est ce qu'on part du principe qu'il n'est plus dans la station de la maison ?
            duree                = duree / 10 # sinon un intervalle (entre 0.1 et 0.3). Durée calculée en minutes ?
            #self.durees.append( duree)
            self.heure_d_arrivee =  self.heure_de_depart + duree
            self.nb_km_trajet    = self.nb_km_trajet / float(10)
            self.log_debug(u"velo defaillant <0.3, rendu a la meme station :-( ")
            self.rendre_vite_velo(station)
        elif velo.performance <0.5:
            duree                = duree *1.5
            #self.durees.append( duree)
            self.nb_km_trajet    = self.nb_km_trajet 
            self.heure_d_arrivee =  self.heure_de_depart + duree 
            self.log_debug(u"velo defaillant <0.5")
        else:
            pass
            #self.durees.append( duree)




    def rendre_vite_velo(self, station):        
        import time
        
        if not self.sur_velo:
            self.log_debug(u"pas en chemin")    
            return 0
        
        if time.time() < self.heure_d_arrivee: # si le vélo n'est pas encore arrivé, comment on peut avoir heure d'arrivée pour comparer ?
            self.log_debug(u"pas encore arrive")
            return
        
        if self.a_la_maison:
            station = self.station_maison
            elem_de = "station_maison"
        else:
            station = self.station_travail
            elem_de = "station_travail"
        self.log_debug(u"self.a_la_maison = %s"%self.a_la_maison)    
        
        rendu = False
        for local_station in station.nearest:
            if local_station.rendre_velo(self.velo, self.nb_km_trajet):
                self.log_debug(u"velo rendu sur la station %s ( a la maison = %s) (elem de %s)"%(local_station, self.a_la_maison, elem_de))    
                rendu = True
                break
            else:
                self.log_debug(u"impossible de rendre sur ,%s ( a la maison = %s)"%(local_station, self.a_la_maison))    
        if not rendu:
            return
                        
        self.last_rendu = time.time()
        duree_constatee = self.last_rendu - self.heure_de_depart
        trajet          = (self.heure_de_depart, self.heure_d_arrivee, self.identifiant, self.nb_km_trajet, self.velo.nom )
        self.sur_velo  = False
        self.nb_trajet = self.nb_trajet + 1
        self.log_rendu()
        self.trajet_courant.fin(local_station)
        self.velo      = False
        
        #self.trajets.append(trajet)
    def rendre_velo(self):        
        import time
        
        if not self.sur_velo:
            self.log_debug(u"pas en chemin")    
            return 0
        
        if time.time() < self.heure_d_arrivee:
            self.log_debug(u"pas encore arrive")
            return
        
        if self.a_la_maison:
            station = self.station_maison
            elem_de = "station_maison"
        else:
            station = self.station_travail
            elem_de = "station_travail"
        self.log_debug(u"self.a_la_maison = %s"%self.a_la_maison)    
        
        rendu = False
        for local_station in station.nearest:
            if local_station.rendre_velo(self.velo, self.nb_km_trajet):
                self.log_debug(u"velo rendu sur la station %s ( a la maison = %s) (elem de %s)"%(local_station, self.a_la_maison, elem_de))    
                rendu = True
                break
            else:
                self.log_debug(u"impossible de rendre sur ,%s ( a la maison = %s)"%(local_station, self.a_la_maison))    
        if not rendu:
            return
                        
        self.last_rendu = time.time()
        duree_constatee = self.last_rendu - self.heure_de_depart
        trajet          = (self.heure_de_depart, self.heure_d_arrivee, self.identifiant, self.nb_km_trajet, self.velo.nom )
        self.sur_velo  = False
        self.nb_trajet = self.nb_trajet + 1
        self.log_rendu()
        self.trajet_courant.fin(local_station)
        self.velo      = False
        
        #self.trajets.append(trajet)
        
            
    def __str__(self):
        return self.identifiant
    def log_cycliste(self):

        to_print = u"%s,%s,%s,%s,%s,%s,%s"%(    self.identifiant   ,self.sportif     ,
                                                 self.age         ,self.sexe        ,
                                                 self.nb_km       ,self.vitesse     , self.attente )
        
        self.logger_cycliste.log(to_print)
            
    def log_prise(self, action="prise"):

        to_print = u"%s,%s,%s,%s"%( self.identifiant,self.heure_de_depart, self.velo.nom, action)
        self.logger_prise.log(to_print)
            
    def log_rendu(self, action="rendu"):

        to_print = u"%s,%s,%s,%s,%s\n"%( self.identifiant, self.heure_de_depart, 
                                       self.heure_d_arrivee,  self.nb_km_trajet, self.velo.nom )

        self.logger_rendu.log(to_print)
        
    def log_debug(self, message):
        from time import time
        to_print = u"%s,%04d, %s,%s"% (self.identifiant,self.n_message, time() , message)
        self.n_message = self.n_message + 1
        self.logger_debug.log(to_print)
    
        


In [7]:
class trajet():
    def __init__(self, cycliste, velo, station):
        from time import time
        self.cycliste        = cycliste
        self.velo            = velo
        self.station_depart  = station
        self.heure_de_depart = time()
        champs = ["station_depart", "cycliste", "velo", "heure_de_depart", "heure_de_fin", "duree", "distance", "station_arrivee"]
        self.logger          = logger("./../logs/trajets.csv", header =",".join(champs))
        
    def fin(self, station):
        self.heure_de_fin     = time()
        self.duree            = self.heure_de_fin - self.heure_de_depart
        self.station_arrivee  = station
        A = self.station_depart.position
        B = self.station_arrivee.position
        self.distance = math.sqrt( (A[0]-B[0])**2 + (A[1]-B[1])**2 )
        champs = ["station_depart", "cycliste", "velo", "heure_de_depart", "heure_de_fin", "duree", "distance", "station_arrivee"]
        to_print = ",".join(["%s"%self.__dict__[x] for x in champs])
        self.logger.log(to_print)


# -1) Velo

In [8]:
class Velo:

    def __init__(self, nom, station):
        from scipy.stats import norm
        import time 
        performance            = norm( loc =0.9, scale=0.2 )
        
        self.nom               = "%s_%s"%(nom, time.time())
        self.performance       = performance.rvs(1)[0]
        self.station           = station
        self.degradation       = 0 # On part du principe qu'il n'y a pas de dégradation à l'initiale ?
        self.performances      = [] # A quoi ça sert ?
        self.debug             = True # False
        self.nb_km_trajet      = 0
        self.heures_rendu      = []
        self.disponible        = True
        self.logger_reparation = logger("./../logs/velo_reparations.csv", header = "velo,n_message,time,performance")
        self.logger_etat       = logger("./../logs/velos_etats.csv", header = "velo,n_message,time,station.nom,performance,nb_km_trajet")
                
        

        self.probleme_list     = self.get_problemes_list()
        self.n_message         = -1

    def get_problemes_list(self):
        """
        Créé le tableau de dégradations possible pour un vélo.
        """
        import math
        problemes       = [0] * int(math.ceil((50*self.performance)))
        problemes_bis   = {u"pedale" : 0.2, u"roue"  : 1 , u"degonfle" : 0.3, u"freins" : 0.05 , 0 : 0}
        problemes.extend(problemes_bis.values())
        return problemes
        
    def log_reparation(self):
        import time
        self.n_message = self.n_message + 1
        reparation     = (self.nom,self.n_message, time.time(),self.performance)
        to_print       = u"%s,%s, %s,%s"%reparation
        self.logger_reparation.log(to_print)
        

    def log_etat(self):
        from time import time
        self.n_message = self.n_message + 1
        to_print = u"%s,%s,%s,%s,%s,%s\n"%(   self.nom           ,
                                            self.n_message,
                                           time()            ,  
                                           self.station.nom  ,
                                           self.performance  ,
                                           self.nb_km_trajet )
        self.logger_etat.log(to_print)
    
    def rendu(self, station, nb_km_trajet):
        import time
        degradation       = random.choice(self.probleme_list)        
        self.disponible   = True
        self.performance  = self.performance - self.performance*degradation                                        
        self.nb_km_trajet = nb_km_trajet
        self.station      = station
        self.log_etat()
        if 900 < random.randint(0, 1000 ) :
            self.performance  = 1
            self.log_reparation()
        
        

    def __str__(self):
        return "%s"%self.nom



# -1 ) Station

In [9]:
class Station:
    def __init__(self, parameters, debug=False ):
        
        import random
        import time
        
        self.nom               = parameters[0]
        self.position          = parameters[1]
        self.nb_plot           = random.choice([10,15,20, 30]) # Nombre de places 
        self.nb_libre          = 0 # Nombre de places libres
        self.nb_velos          = self.nb_plot # On part du principe où toutes les places sont prises
        self.velos             = []     # Création d'une liste vide
        self.n_message         = -1 # ?
        self.debug             = False
        self.avaries           = [] # Avarie sur le vélo ?
        self.arrete            = False
        self.liste_d_avaries   = []
        self.nb_fois_en_arret  = 0
        self.logger_dispos     = logger("./../logs/stations_dispos.csv", header = "nom,n_message,time,nb_plot,nb_libre,nb_velos")
        self.logger_reparation = logger("./../logs/stations_reparations.csv")
        self.logger_avarie     = logger("./../logs/stations_avarie.csv", header = "nom,n_message,time,avarie")
        
        self.log_dispo()

        noms = get_names() # la définition de get_names est plus bas dans une autre cellule
        for n in range(self.nb_velos ):
            nom_velo= u"velo_"+"".join(["%s"%x for x in random.choice(noms)])
            self.velos.append(Velo(nom_velo , self))
        

    def log_reparation(self):
        self.log_dispo()
            
            
    def log_dispo(self):
        from time import time
        self.n_message = self.n_message + 1 # sachant qu'on commence à -1 donc on commence à 0
        dispo =(self.nom,self.n_message, time(),self.nb_plot, self.nb_libre, self.nb_velos)
        # On décrit la disponibilité de la station : le nom, combien de places libres...
        to_print = u"%s,%s,%s,%s,%s,%s"%dispo # On imprime le message résumant tout ce qui est en haut
        
        self.logger_dispos.log(to_print)
            
    def log_avarie(self, avarie):
        from time import time
        self.n_message = self.n_message + 1
        to_print = u"%s,%s,%s,%s"%(self.nom,self.n_message, time(), avarie) 
        
        self.logger_avarie.log(to_print)

    
    def avarie_possible(self):
        import math
        import random
        import time
        problemes   = { "plot"       : range(0, 20) , # Le nombre de places possibles
                       "half"        : range(20,30) , # ?
                       "network"     : range(30,35) , # problème de réseau
                       "electricite" : range(35,60) , 
                       "bug"         : range(60,90) } # bug de quelle nature ?
        zero     = 0
        mil      = 1000
        cent_mil = 100 * mil 
        
        for k,v in problemes.iteritems():
            if k in self.liste_d_avaries:
                r = random.randint(mil, cent_mil)
                new_range = range(r, r+30)
                problemes[k].extend(new_range)
        
        alea = random.randint(zero,cent_mil)
        avarie = False
        for k,v in problemes.iteritems():
            if alea in v:
                avarie = k
                
        if avarie:
            self.avaries.extend([avarie])
            if   avarie == "plot" : self.nb_libre = self.nb_libre -1 # Avarie sur une place
            elif avarie == "half" : self.nb_libre = math.floor(self.nb_libre - (self.nb_plot / float(2)))
            elif avarie == "bug"  : self.nb_libre = self.nb_libre - random.randint(0, self.nb_libre)
            elif avarie == "network" or avarie == "electricite": # Avarie sur toute la station
                self.nb_libre = 0
                self.arrete = True
                
            if self.nb_libre < 0: # On peut avoir un nombre de places libres inférieur à 0 ?
                self.nb_libre = 0            
            self.log_dispo()

            if avarie:
                self.log_avarie("%s"%avarie)
            
    def rendre_velo(self, velo, nb_km_trajet):
        import time
        self.avarie_possible()
        if self.nb_libre >0:
            self.velos.append(velo)
            velo.rendu(self, nb_km_trajet)
            self.nb_velos = len(self.velos)
            self.nb_libre = self.nb_libre - 1 # A chaque fois que je retourne un vélo, il enlève une place
            self.log_dispo()
            return 1 # Pour dire que j'ai un vélo disponible
        if 9500 < random.randint(0, 10000 ) :
            self.reparer() # ?
        return 0
    
    def reparer(self):
        self.nb_libre = self.nb_plot - self.nb_velos
        self.arrete   = False
        self.log_reparation()
        
    def prendre_velo(self):
        """
        retourne un vélo ou 0 en cas d'erreur.
        """
        import time
        self.avarie_possible()
        if self.velos and not self.arrete :
            to_return     = self.velos.pop()
            self.nb_velos = len(self.velos)
            self.nb_libre = self.nb_libre + 1
            self.log_dispo()
            return to_return
        
        if self.arrete:
            self.nb_fois_en_arret += 1 # erreur codage ?
        
        if self.nb_fois_en_arret > 10:
            self.reparer()

        return 0
    
    def get_nearest_station(self): # dans un carré ?
        x = self.position[0]
        y = self.position[1]
        deplacement_x = [-1, 0, 1]
        deplacement_y = [-1, 0, 1]
        deplacements  = [ (x_proche , y_proche) for x_proche in deplacement_x for y_proche in  deplacement_y if x_proche or y_proche]
        positions_proches = [(x +  a , y +  b) for a,b in  deplacements ]
        nearests = []
        for x2, y2 in positions_proches:
            if x2 + x < 0 or y2 + y < 0:
                continue 
            position_la_plus_proche = x2 * cote_len  + y2
            if 0 <= position_la_plus_proche and position_la_plus_proche < len(stations):
                nearests.append(stations[position_la_plus_proche])
        return nearests
        
                
    def __str__(self):
        return u"%s"%(self.nom)


# 0) get_names

In [10]:
def get_names(nb_lettres=5, nb_noms = 15000, prefix=""):
    """
    retourne n mot de nb_lettres avec prefix.
    """
    import itertools
    from random import shuffle
    lettres = "azertyuiopqsdfghjklmwxcvbn1234567890"
    names   = [] # pour initialiser ?
    for i in itertools.combinations(lettres, nb_lettres): # combinaisons possibles : 5 ** len(lettres)
        name = "".join(i)
        name = prefix + name
        names.append(name)
        nb_noms = nb_noms -1
        if nb_noms <2:
            break
    shuffle(names)
    return names

# 0) création des stations

In [11]:
import math

In [12]:
deplacement_x = [-1, 0, 1]
deplacement_y = [-1, 0, 1]

In [13]:
from time import time
import multiprocessing
nb_cpu       = 4
nb_station   = 100
debut        = time()
process_pool = multiprocessing.Pool(nb_cpu)
debut        = time()
names        = get_names()
cote_len     = int(math.ceil(math.sqrt(nb_station)))
positions    = [ (longitude, lattitude) for longitude in range(cote_len) for lattitude in range(cote_len)]
parameters   = [(names[i], positions[i]) for i in range(nb_station)]

stations     = [Station(p) for p in parameters]
for x in stations:
    x.nearest = x.get_nearest_station()
nb_velos     = sum([len(station.velos) for station in stations])
duree = time() - debut
print ("duree = %s pour %s cree soit %s sec / unite"%(duree, nb_velos, duree/nb_velos))


duree = 5.533316373825073 pour 1885 cree soit 0.0029354463521618426 sec / unite


# Creation des cycliste

In [14]:
aller_a = []
probas  = {}
n = -1
for station in stations:
    n           = n + 1
    milieu      =  cote_len / 2 
    centre      = (milieu, milieu)
    adjacent_1  = (station.position[0] - milieu)
    adjacent_2  = (station.position[1] - milieu)
    hypothenuse = math.sqrt( adjacent_1*adjacent_1 + adjacent_2 *adjacent_2 ) 
    probas      = int(math.ceil(milieu - math.floor(hypothenuse) + 2))
    aller_a.extend([station]*probas)    

In [15]:
names        = get_names(5, nb_velos*11)

In [16]:
debut        = time()
n            = 4
multiple     = nb_velos*2
process_pool = multiprocessing.Pool(n)
names        = get_names(5, multiple)
noms         = [(names[i], random.choice(stations), random.choice(aller_a)) for i in range(multiple-1)]
cyclistes    = [Cycliste(noms[i]) for i in range(int(math.floor(nb_velos*1.3)) )]
duree        = time() - debut
print ("duree = %s pour %s cree soit %s sec / unite"%(duree, len(cyclistes), duree/nb_velos))


duree = 78.63949799537659 pour 2450 cree soit 0.041718566575796596 sec / unite


In [17]:
velos = [x.velos for x in stations]

# voyages

In [18]:
if False:
    to_fetch = ["nb_plot", "nb_libre", "nb_velos", "position"]
    for station in stations[:2]:
        for item in to_fetch:
            print(item, station.__dict__[item])


In [19]:
if False:
    to_fetch = ["disponible"] #, "nb_km_trajet"]
    for velo in velos:
        data = [x.__dict__[info] for x in velo for info in to_fetch  ]
        print (data)

In [20]:
from time import time
import multiprocessing
import math
from time import time

In [ ]:
from time import gmtime, strftime

In [ ]:
depart = time()
print ("debut a ", strftime("%Y-%m-%d %H:%M:%S", gmtime()))
n = 0  
a         = time()
while time() < depart + 10000 :     
    old_nb_trajet = sum([cycliste.nb_trajet for cycliste in cyclistes])
    en_route = filter(lambda cycliste:     cycliste.sur_velo, cyclistes)
    a_pied   = filter(lambda cycliste: not cycliste.sur_velo, cyclistes)
    
    map(lambda cycliste: cycliste.rendre_velo(), en_route  )
    map(lambda cycliste: cycliste.prend_velo(),  a_pied    )
    
    new_nb_trajet =  sum([cycliste.nb_trajet for cycliste in cyclistes]) - old_nb_trajet
    
    if n%10 ==0:
        duree_totale = time()-a
        nb_arrete = sum([ s.__dict__['arrete'] for s in stations ])
        print ("(tour n°%03d)%03d/% 3.2f| %s "%(n, new_nb_trajet, duree_totale, nb_arrete))
        a         = time()

    n += 1
    
print ("*"*30)
print ("fini")
print ("*"*30)
print ("fin a ", strftime("%Y-%m-%d %H:%M:%S", gmtime()))

debut a  2018-01-20 10:32:24
(tour n°000)000/ 0.00| 0 
(tour n°010)000/ 0.01| 0 
(tour n°020)000/ 0.01| 0 
(tour n°030)000/ 0.00| 0 
(tour n°040)000/ 0.00| 0 
(tour n°050)000/ 0.00| 0 
(tour n°060)000/ 0.00| 0 
(tour n°070)000/ 0.00| 0 
(tour n°080)000/ 0.00| 0 
(tour n°090)000/ 0.00| 0 
(tour n°100)000/ 0.00| 0 
(tour n°110)000/ 0.01| 0 
(tour n°120)000/ 0.01| 0 
(tour n°130)000/ 0.00| 0 
(tour n°140)000/ 0.01| 0 
(tour n°150)000/ 0.01| 0 
(tour n°160)000/ 0.01| 0 
(tour n°170)000/ 0.02| 0 
(tour n°180)000/ 0.01| 0 
(tour n°190)000/ 0.01| 0 
(tour n°200)000/ 0.01| 0 
(tour n°210)000/ 0.02| 0 
(tour n°220)000/ 0.01| 0 
(tour n°230)000/ 0.01| 0 
(tour n°240)000/ 0.01| 0 
(tour n°250)000/ 0.01| 0 
(tour n°260)000/ 0.01| 0 
(tour n°270)000/ 0.01| 0 
(tour n°280)000/ 0.03| 0 
(tour n°290)000/ 0.02| 0 
(tour n°300)000/ 0.02| 0 
(tour n°310)000/ 0.01| 0 
(tour n°320)000/ 0.04| 0 
(tour n°330)000/ 0.02| 0 
(tour n°340)000/ 0.03| 0 
(tour n°350)000/ 0.01| 0 
(tour n°360)000/ 0.01| 0 
(tour n°3

(tour n°3390)000/ 0.00| 0 
(tour n°3400)000/ 0.00| 0 
(tour n°3410)000/ 0.01| 0 
(tour n°3420)000/ 0.01| 0 
(tour n°3430)000/ 0.01| 0 
(tour n°3440)000/ 0.01| 0 
(tour n°3450)000/ 0.02| 0 
(tour n°3460)000/ 0.01| 0 
(tour n°3470)000/ 0.01| 0 
(tour n°3480)000/ 0.02| 0 
(tour n°3490)000/ 0.01| 0 
(tour n°3500)000/ 0.02| 0 
(tour n°3510)000/ 0.01| 0 
(tour n°3520)000/ 0.01| 0 
(tour n°3530)000/ 0.03| 0 
(tour n°3540)000/ 0.02| 0 
(tour n°3550)000/ 0.01| 0 
(tour n°3560)000/ 0.01| 0 
(tour n°3570)000/ 0.01| 0 
(tour n°3580)000/ 0.01| 0 
(tour n°3590)000/ 0.01| 0 
(tour n°3600)000/ 0.00| 0 
(tour n°3610)000/ 0.01| 0 
(tour n°3620)000/ 0.01| 0 
(tour n°3630)000/ 0.01| 0 
(tour n°3640)000/ 0.00| 0 
(tour n°3650)000/ 0.01| 0 
(tour n°3660)000/ 0.01| 0 
(tour n°3670)000/ 0.01| 0 
(tour n°3680)000/ 0.01| 0 
(tour n°3690)000/ 0.01| 0 
(tour n°3700)000/ 0.01| 0 
(tour n°3710)000/ 0.01| 0 
(tour n°3720)000/ 0.01| 0 
(tour n°3730)000/ 0.01| 0 
(tour n°3740)000/ 0.02| 0 
(tour n°3750)000/ 0.01| 0 
(

(tour n°6610)000/ 0.01| 0 
(tour n°6620)000/ 0.01| 0 
(tour n°6630)000/ 0.01| 0 
(tour n°6640)000/ 0.01| 0 
(tour n°6650)000/ 0.01| 0 
(tour n°6660)000/ 0.01| 0 
(tour n°6670)000/ 0.01| 0 
(tour n°6680)000/ 0.01| 0 
(tour n°6690)000/ 0.01| 0 
(tour n°6700)000/ 0.00| 0 
(tour n°6710)000/ 0.00| 0 
(tour n°6720)000/ 0.01| 0 
(tour n°6730)000/ 0.01| 0 
(tour n°6740)000/ 0.00| 0 
(tour n°6750)000/ 0.01| 0 
(tour n°6760)000/ 0.01| 0 
(tour n°6770)000/ 0.01| 0 
(tour n°6780)000/ 0.00| 0 
(tour n°6790)000/ 0.01| 0 
(tour n°6800)000/ 0.02| 0 
(tour n°6810)000/ 0.01| 0 
(tour n°6820)000/ 0.01| 0 
(tour n°6830)000/ 0.01| 0 
(tour n°6840)000/ 0.01| 0 
(tour n°6850)000/ 0.00| 0 
(tour n°6860)000/ 0.01| 0 
(tour n°6870)000/ 0.01| 0 
(tour n°6880)000/ 0.01| 0 
(tour n°6890)000/ 0.03| 0 
(tour n°6900)000/ 0.01| 0 
(tour n°6910)000/ 0.03| 0 
(tour n°6920)000/ 0.02| 0 
(tour n°6930)000/ 0.01| 0 
(tour n°6940)000/ 0.02| 0 
(tour n°6950)000/ 0.02| 0 
(tour n°6960)000/ 0.02| 0 
(tour n°6970)000/ 0.01| 0 
(

(tour n°10420)000/ 0.01| 0 
(tour n°10430)000/ 0.01| 0 
(tour n°10440)000/ 0.01| 0 
(tour n°10450)000/ 0.01| 0 
(tour n°10460)000/ 0.01| 0 
(tour n°10470)000/ 0.01| 0 
(tour n°10480)000/ 0.01| 0 
(tour n°10490)000/ 0.01| 0 
(tour n°10500)000/ 0.01| 0 
(tour n°10510)000/ 0.01| 0 
(tour n°10520)000/ 0.01| 0 
(tour n°10530)000/ 0.01| 0 
(tour n°10540)000/ 0.01| 0 
(tour n°10550)000/ 0.01| 0 
(tour n°10560)000/ 0.01| 0 
(tour n°10570)000/ 0.01| 0 
(tour n°10580)000/ 0.01| 0 
(tour n°10590)000/ 0.01| 0 
(tour n°10600)000/ 0.01| 0 
(tour n°10610)000/ 0.01| 0 
(tour n°10620)000/ 0.01| 0 
(tour n°10630)000/ 0.01| 0 
(tour n°10640)000/ 0.01| 0 
(tour n°10650)000/ 0.01| 0 
(tour n°10660)000/ 0.01| 0 
(tour n°10670)000/ 0.01| 0 
(tour n°10680)000/ 0.01| 0 
(tour n°10690)000/ 0.01| 0 
(tour n°10700)000/ 0.00| 0 
(tour n°10710)000/ 0.01| 0 
(tour n°10720)000/ 0.01| 0 
(tour n°10730)000/ 0.01| 0 
(tour n°10740)000/ 0.01| 0 
(tour n°10750)000/ 0.01| 0 
(tour n°10760)000/ 0.01| 0 
(tour n°10770)000/ 0

(tour n°13900)000/ 0.01| 0 
(tour n°13910)000/ 0.01| 0 
(tour n°13920)000/ 0.01| 0 
(tour n°13930)000/ 0.01| 0 
(tour n°13940)000/ 0.00| 0 
(tour n°13950)000/ 0.01| 0 
(tour n°13960)000/ 0.03| 0 
(tour n°13970)000/ 0.01| 0 
(tour n°13980)000/ 0.01| 0 
(tour n°13990)000/ 0.01| 0 
(tour n°14000)000/ 0.01| 0 
(tour n°14010)000/ 0.01| 0 
(tour n°14020)000/ 0.01| 0 
(tour n°14030)000/ 0.01| 0 
(tour n°14040)000/ 0.01| 0 
(tour n°14050)000/ 0.01| 0 
(tour n°14060)000/ 0.01| 0 
(tour n°14070)000/ 0.02| 0 
(tour n°14080)000/ 0.01| 0 
(tour n°14090)000/ 0.01| 0 
(tour n°14100)000/ 0.00| 0 
(tour n°14110)000/ 0.01| 0 
(tour n°14120)000/ 0.01| 0 
(tour n°14130)000/ 0.01| 0 
(tour n°14140)000/ 0.01| 0 
(tour n°14150)000/ 0.01| 0 
(tour n°14160)000/ 0.01| 0 
(tour n°14170)000/ 0.00| 0 
(tour n°14180)000/ 0.01| 0 
(tour n°14190)000/ 0.01| 0 
(tour n°14200)000/ 0.01| 0 
(tour n°14210)000/ 0.01| 0 
(tour n°14220)000/ 0.01| 0 
(tour n°14230)000/ 0.01| 0 
(tour n°14240)000/ 0.01| 0 
(tour n°14250)000/ 0

...

(tour n°2317940)000/ 0.02| 0 
(tour n°2317950)000/ 0.02| 0 
(tour n°2317960)000/ 0.01| 0 
(tour n°2317970)000/ 0.02| 0 
(tour n°2317980)000/ 0.01| 0 
(tour n°2317990)000/ 0.04| 0 
(tour n°2318000)000/ 0.02| 0 
(tour n°2318010)000/ 0.02| 0 
(tour n°2318020)000/ 0.01| 0 
(tour n°2318030)000/ 0.03| 0 
(tour n°2318040)000/ 0.03| 0 
(tour n°2318050)000/ 0.03| 0 
(tour n°2318060)000/ 0.03| 0 
(tour n°2318070)000/ 0.02| 0 
(tour n°2318080)000/ 0.01| 0 
(tour n°2318090)000/ 0.01| 0 
(tour n°2318100)000/ 0.01| 0 
(tour n°2318110)000/ 0.01| 0 
(tour n°2318120)000/ 0.01| 0 
(tour n°2318130)000/ 0.01| 0 
(tour n°2318140)000/ 0.01| 0 
(tour n°2318150)000/ 0.01| 0 
(tour n°2318160)000/ 0.02| 0 
(tour n°2318170)000/ 0.05| 0 
(tour n°2318180)000/ 0.02| 0 
(tour n°2318190)000/ 0.01| 0 
(tour n°2318200)000/ 0.01| 0 
(tour n°2318210)000/ 0.01| 0 
(tour n°2318220)000/ 0.01| 0 
(tour n°2318230)000/ 0.01| 0 
(tour n°2318240)000/ 0.04| 0 
(tour n°2318250)000/ 0.02| 0 
(tour n°2318260)000/ 0.03| 0 
(tour n°23

(tour n°2320680)000/ 0.02| 0 
(tour n°2320690)000/ 0.01| 0 
(tour n°2320700)000/ 0.01| 0 
(tour n°2320710)000/ 0.01| 0 
(tour n°2320720)000/ 0.01| 0 
(tour n°2320730)000/ 0.01| 0 
(tour n°2320740)000/ 0.51| 0 
(tour n°2320750)000/ 0.08| 0 
(tour n°2320760)000/ 0.04| 0 
(tour n°2320770)000/ 0.03| 0 
(tour n°2320780)000/ 0.03| 0 
(tour n°2320790)000/ 0.02| 0 
(tour n°2320800)000/ 0.02| 0 
(tour n°2320810)000/ 0.03| 0 
(tour n°2320820)000/ 0.05| 0 
(tour n°2320830)000/ 0.02| 0 
(tour n°2320840)000/ 0.13| 0 
(tour n°2320850)000/ 0.10| 0 
(tour n°2320860)000/ 0.03| 0 
(tour n°2320870)000/ 0.03| 0 
(tour n°2320880)000/ 0.02| 0 
(tour n°2320890)000/ 0.02| 0 
(tour n°2320900)000/ 0.03| 0 
(tour n°2320910)000/ 0.02| 0 
(tour n°2320920)000/ 0.02| 0 
(tour n°2320930)000/ 0.02| 0 
(tour n°2320940)000/ 0.02| 0 
(tour n°2320950)000/ 0.02| 0 
(tour n°2320960)000/ 0.02| 0 
(tour n°2320970)000/ 0.02| 0 
(tour n°2320980)000/ 0.02| 0 
(tour n°2320990)000/ 0.04| 0 
(tour n°2321000)000/ 0.02| 0 
(tour n°23

(tour n°2323500)000/ 0.02| 0 
(tour n°2323510)000/ 0.01| 0 
(tour n°2323520)000/ 0.01| 0 
(tour n°2323530)000/ 0.02| 0 
(tour n°2323540)000/ 0.01| 0 
(tour n°2323550)000/ 0.01| 0 
(tour n°2323560)000/ 0.01| 0 
(tour n°2323570)000/ 0.01| 0 
(tour n°2323580)000/ 0.01| 0 
(tour n°2323590)000/ 0.01| 0 
(tour n°2323600)000/ 0.01| 0 
(tour n°2323610)000/ 0.01| 0 
(tour n°2323620)000/ 0.01| 0 
(tour n°2323630)000/ 0.01| 0 
(tour n°2323640)000/ 0.01| 0 
(tour n°2323650)000/ 0.00| 0 
(tour n°2323660)000/ 0.01| 0 
(tour n°2323670)000/ 0.01| 0 
(tour n°2323680)000/ 0.01| 0 
(tour n°2323690)000/ 0.01| 0 
(tour n°2323700)000/ 0.01| 0 
(tour n°2323710)000/ 0.01| 0 
(tour n°2323720)000/ 0.00| 0 
(tour n°2323730)000/ 0.01| 0 
(tour n°2323740)000/ 0.00| 0 
(tour n°2323750)000/ 0.00| 0 
(tour n°2323760)000/ 0.01| 0 
(tour n°2323770)000/ 0.01| 0 
(tour n°2323780)000/ 0.01| 0 
(tour n°2323790)000/ 0.00| 0 
(tour n°2323800)000/ 0.01| 0 
(tour n°2323810)000/ 0.01| 0 
(tour n°2323820)000/ 0.01| 0 
(tour n°23

(tour n°2326440)000/ 0.00| 0 
(tour n°2326450)000/ 0.03| 0 
(tour n°2326460)000/ 0.02| 0 
(tour n°2326470)000/ 0.03| 0 
(tour n°2326480)000/ 0.02| 0 
(tour n°2326490)000/ 0.02| 0 
(tour n°2326500)000/ 0.02| 0 
(tour n°2326510)000/ 0.01| 0 
(tour n°2326520)000/ 0.02| 0 
(tour n°2326530)000/ 0.03| 0 
(tour n°2326540)000/ 0.04| 0 
(tour n°2326550)000/ 0.00| 0 
(tour n°2326560)000/ 0.00| 0 
(tour n°2326570)000/ 0.00| 0 
(tour n°2326580)000/ 0.02| 0 
(tour n°2326590)000/ 0.02| 0 
(tour n°2326600)000/ 0.00| 0 
(tour n°2326610)000/ 0.00| 0 
(tour n°2326620)000/ 0.02| 0 
(tour n°2326630)000/ 0.00| 0 
(tour n°2326640)000/ 0.02| 0 
(tour n°2326650)000/ 0.00| 0 
(tour n°2326660)000/ 0.02| 0 
(tour n°2326670)000/ 0.00| 0 
(tour n°2326680)000/ 0.02| 0 
(tour n°2326690)000/ 0.02| 0 
(tour n°2326700)000/ 0.02| 0 
(tour n°2326710)000/ 0.00| 0 
(tour n°2326720)000/ 0.02| 0 
(tour n°2326730)000/ 0.00| 0 
(tour n°2326740)000/ 0.02| 0 
(tour n°2326750)000/ 0.00| 0 
(tour n°2326760)000/ 0.00| 0 
(tour n°23

(tour n°2329440)000/ 0.02| 0 
(tour n°2329450)000/ 0.00| 0 
(tour n°2329460)000/ 0.02| 0 
(tour n°2329470)000/ 0.02| 0 
(tour n°2329480)000/ 0.02| 0 
(tour n°2329490)000/ 0.00| 0 
(tour n°2329500)000/ 0.00| 0 
(tour n°2329510)000/ 0.02| 0 
(tour n°2329520)000/ 0.00| 0 
(tour n°2329530)000/ 0.00| 0 
(tour n°2329540)000/ 0.00| 0 
(tour n°2329550)000/ 0.02| 0 
(tour n°2329560)000/ 0.02| 0 
(tour n°2329570)000/ 0.00| 0 
(tour n°2329580)000/ 0.02| 0 
(tour n°2329590)000/ 0.00| 0 
(tour n°2329600)000/ 0.00| 0 
(tour n°2329610)000/ 0.00| 0 
(tour n°2329620)000/ 0.02| 0 
(tour n°2329630)000/ 0.00| 0 
(tour n°2329640)000/ 0.00| 0 
(tour n°2329650)000/ 0.02| 0 
(tour n°2329660)000/ 0.00| 0 
(tour n°2329670)000/ 0.00| 0 
(tour n°2329680)000/ 0.02| 0 
(tour n°2329690)000/ 0.00| 0 
(tour n°2329700)000/ 0.03| 0 
(tour n°2329710)000/ 0.03| 0 
(tour n°2329720)000/ 0.02| 0 
(tour n°2329730)000/ 0.02| 0 
(tour n°2329740)000/ 0.03| 0 
(tour n°2329750)000/ 0.02| 0 
(tour n°2329760)000/ 0.03| 0 
(tour n°23

In [ ]:
print ("fini 2")

In [ ]:
save_network = True
if save_network:
    import pickle
    path_to_save_stations = "./../logs/stations.csv"
    with open(path_to_save_stations, "w") as output_file:
        pickle.dump(stations, output_file)
    path_to_save_cyclistes = "./../logs/cyclistes.csv"
    with open(path_to_save_cyclistes, "w") as output_file:
        pickle.dump(cyclistes, output_file)

In [ ]:
if False :
    load_network   = False
    nb_de_secondes = 1800
    try:
        if load_network:
            stations2  = pickle.load(open(path_to_save_stations ))
            cyclistes2 = pickle.load(open(path_to_save_cyclistes))
        depart     = time()
        print "debut a ", strftime("%Y-%m-%d %H:%M:%S", gmtime())
        n = 0  
        a = time()
        while time() < depart + nb_de_secondes :     
            old_nb_trajet = sum([cycliste.nb_trajet for cycliste in cyclistes2])
            en_route = filter(lambda cycliste:     cycliste.sur_velo, cyclistes2)
            a_pied   = filter(lambda cycliste: not cycliste.sur_velo, cyclistes2)

            map(lambda cycliste: cycliste.rendre_velo(), en_route  )
            map(lambda cycliste: cycliste.prend_velo(),  a_pied    )

            new_nb_trajet =  sum([cycliste.nb_trajet for cycliste in cyclistes2]) - old_nb_trajet

            if n%10 ==0:
                duree_totale = time()-a
                nb_arrete = sum([ s.__dict__['arrete'] for s in stations2 ])
                print ("(tour n°%03d)%03d/% 3.2f| %s "%(n, new_nb_trajet, duree_totale, nb_arrete))
                a = time()

            n += 1

        print ("*"*30)
        print ("fini")
        print ("*"*30)
        print ("fin a ", strftime("%Y-%m-%d %H:%M:%S", gmtime()))
    except:
        print ("on enregistre la situation")
        import pickle
        path_to_save_stations = "./../logs/stations_%s.csv"%time()
        with open(path_to_save_stations, "w") as output_file:
            pickle.dump(stations, output_file)
        path_to_save_cyclistes = "./../logs/cyclistes_%s.csv"%time()
        with open(path_to_save_cyclistes, "w") as output_file:
            pickle.dump(cyclistes, output_file)    